In [1]:
import numpy as np 

import pandas as pd 
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests
from pandas.io.json import json_normalize

import matplotlib.cm as cm
import matplotlib.colors as colors

from sklearn.cluster import KMeans

import folium 

In [2]:
website = 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'
page = requests.get(website)


In [3]:
from bs4 import BeautifulSoup
soup = BeautifulSoup(page.content, 'html.parser')
print(soup.prettify())

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
 <head>
  <meta charset="utf-8"/>
  <title>
   List of postal codes of Canada: M - Wikipedia
  </title>
  <script>
   document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"4be8faea-0e68-4c1d-85a9-cdf7c27a3898","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_postal_codes_of_Canada:_M","wgTitle":"List of postal codes of Canada: M","wgCurRevisionId":960187814,"wgRevisionId":960187814,"wgArticleId":539066,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Articles with short description","Communications in Ontario","Postal codes in Canada","Toron

In [4]:
text = soup.get_text()
print(text)






List of postal codes of Canada: M - Wikipedia































List of postal codes of Canada: M

From Wikipedia, the free encyclopedia


Jump to navigation
Jump to search
Wikipedia list article
This is a list of postal codes in Canada where the first letter is M. Postal codes beginning with M are located within the city of Toronto in the province of Ontario. Only the first three characters are listed, corresponding to the Forward Sortation Area.
Canada Post provides a free postal code look-up tool on its website,[1] via its applications for such smartphones as the iPhone and BlackBerry,[2]  and sells hard-copy directories and CD-ROMs. Many vendors also sell validation tools, which allow customers to properly match addresses and postal codes. Hard-copy directories can also be consulted in all post offices, and some libraries.

Toronto - 103 FSAs[edit]
Note: There are no rural FSAs in Toronto, hence no postal codes should start with M0. However, the postal code M0R 8T

In [5]:
split = text.split('\n')
split = list(filter(None, split))
for i in range(len(split)):
    if(split[i]=='M1A'):
        start = i
    if(split[i]=='Most populated FSAs[3][edit]'):
        stop=i
        break
split = split[start:stop]
split 


['M1A',
 'Not assigned',
 'Not assigned',
 'M2A',
 'Not assigned',
 'Not assigned',
 'M3A',
 'North York',
 'Parkwoods',
 'M4A',
 'North York',
 'Victoria Village',
 'M5A',
 'Downtown Toronto',
 'Regent Park, Harbourfront',
 'M6A',
 'North York',
 'Lawrence Manor, Lawrence Heights',
 'M7A',
 'Downtown Toronto',
 "Queen's Park, Ontario Provincial Government",
 'M8A',
 'Not assigned',
 'Not assigned',
 'M9A',
 'Etobicoke',
 'Islington Avenue, Humber Valley Village',
 'M1B',
 'Scarborough',
 'Malvern, Rouge',
 'M2B',
 'Not assigned',
 'Not assigned',
 'M3B',
 'North York',
 'Don Mills',
 'M4B',
 'East York',
 'Parkview Hill, Woodbine Gardens',
 'M5B',
 'Downtown Toronto',
 'Garden District, Ryerson',
 'M6B',
 'North York',
 'Glencairn',
 'M7B',
 'Not assigned',
 'Not assigned',
 'M8B',
 'Not assigned',
 'Not assigned',
 'M9B',
 'Etobicoke',
 'West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale',
 'M1C',
 'Scarborough',
 'Rouge Hill, Port Union, Highland Creek',
 'M2C',


In [6]:
columns = 'Borough','Neighborhood','Latitude','Longitude'
df = pd.DataFrame(columns = columns)
df

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

In [7]:
count=0
geolocator = Nominatim(user_agent="toronto")
for i in range(1,len(split)):
    if(i%3==0):
        j = split[i-2],split[i-1]
        if(j[0]!='Not assigned'):
            h = j[1].split(',')
            for i in h:
                address = str(i)+' ,'+str(j[0])
                try:
                    location = geolocator.geocode(address)
                    latitude = location.latitude
                    longitude = location.longitude
                    df.loc[count] = (str(j[0].strip()),str(i.strip()),latitude,longitude)
                    count+=1
                except:
                    address = str(i) + ' ,' + 'Toronto'
                    try:
                        location = geolocator.geocode(address)
                        latitude = location.latitude
                        longitude = location.longitude
                        df.loc[count] = (str(j[0].strip()),str(i.strip()),latitude,longitude)
                        count+=1
                    except:
                        pass

print(df.head())

            Borough      Neighborhood   Latitude  Longitude
0        North York         Parkwoods  43.758800 -79.320197
1        North York  Victoria Village  43.732658 -79.311189
2  Downtown Toronto       Regent Park  43.660706 -79.360457
3  Downtown Toronto      Harbourfront  43.640080 -79.380150
4        North York    Lawrence Manor  43.722079 -79.437507


In [8]:
df = df.sort_values('Borough').reset_index()

In [9]:
address = 'Toronto, Canada'
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


In [10]:
maptor = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(df['Latitude'], df['Longitude'], df['Borough'], df['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(maptor)  
    
maptor

In [11]:
print(df['Borough'].unique())

['Central Toronto' 'Downtown Toronto' 'East Toronto' 'East York'
 'Etobicoke' 'North York' 'Scarborough' 'West Toronto' 'York']


In [12]:
CLIENT_ID = 'GYV2CKD0RBMJPI1IPNQLCR3PMPHMPXWTPP30PENLZRG4OA2Z'
CLIENT_SECRET = '05MQ1RTRYJRSGL4BIWU0GCXY2TQPTHY5Z2DR1R2MC5TH4AE2' # your Foursquare Secret
VERSION = '20202206' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: GYV2CKD0RBMJPI1IPNQLCR3PMPHMPXWTPP30PENLZRG4OA2Z
CLIENT_SECRET:05MQ1RTRYJRSGL4BIWU0GCXY2TQPTHY5Z2DR1R2MC5TH4AE2


In [13]:
def getNearbyVenues(borough,names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for boro,name, lat, lng in zip(borough,names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        try:
            results = requests.get(url).json()["response"]['groups'][0]['items']
            #print(results)
            venues_list.append([(
            boro,
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])
        except:
            pass
        # return only relevant information for each nearby venue
        

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    print(nearby_venues)
    nearby_venues.columns = ['Borough',
        'Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [14]:
# type your answer here
radius = 500
LIMIT = 100
d = getNearbyVenues(df['Borough'],df['Neighborhood'], df['Latitude'], df['Longitude'])

Forest Hill SE
Roselawn
North Midtown
The Annex
Davisville
South Hill
Summerhill West
Lawrence Park
Yorkville
Deer Park
Forest Hill Road Park
Moore Park
Forest Hill North & West
Davisville North
Summerhill East
Rathnelly
Lawrence Park
North Toronto West
Bathurst Quay
Berczy Park
King and Spadina
First Canadian Place
Christie
Underground city
CN Tower
Cabbagetown
St. James Town
Richmond
Adelaide
King
Central Bay Street
Commerce Court
Rosedale
Victoria Hotel
Regent Park
Harbourfront
Queen's Park
South Niagara
Island airport
Design Exchange
Garden District
Church and Wellesley
Ryerson
Railway Lands
Toronto Islands
Union Station
Harbourfront East
Harbord
St. James Town
Chinatown
Harbourfront West
Riverdale
The Beaches
The Danforth West
India Bazaar
The Beaches West
Studio District
Leaside
Woodbine Heights
East Toronto
Broadview North (Old East York)
Thorncliffe Park
Parkview Hill
Woodbine Gardens
Westmount
Kingsway Park South West
St. Phillips
Martin Grove Gardens
Richview Gardens
Kingsvie

In [24]:
toronto_onehot = pd.get_dummies(d[['Venue Category']], prefix="", prefix_sep="")
toronto_onehot['Neighborhood'] = d['Neighborhood']
toronto_onehot['Borough'] = d['Borough']
toronto_onehot.set_index(['Borough','Neighborhood'],inplace=True)
toronto_onehot.sort_index(inplace=True)
toronto_onehot.reset_index(inplace=True)
toronto_onehot.head()

Borough Neighborhood  ATM  Accessories Store  Afghan Restaurant  \
0  Central Toronto   Davisville    0                  0                  0   
1  Central Toronto   Davisville    0                  0                  0   
2  Central Toronto   Davisville    0                  0                  0   
3  Central Toronto   Davisville    0                  0                  0   
4  Central Toronto   Davisville    0                  0                  0   

   African Restaurant  Airport  Airport Service  Airport Terminal  \
0                   0        0                0                 0   
1                   0        0                0                 0   
2                   0        0                0                 0   
3                   0        0                0                 0   
4                   0        0                0                 0   

   American Restaurant  Animal Shelter  Antique Shop  Aquarium  \
0                    0               0             0         0   
1                    0               0             0         0   
2                    0               0             0         0   
3                    0               0             0         0   
4                    0               0             0         0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0                 0                       0            0           0   
1                 0                       0            0           0   
2                 0                       0            0           0   
3                 0                       0            0           0   
4                 0                       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Dealership  \
0                    0                 0                   0                0   
1                    0                 0                   0                0   
2                    0                 0                   0                0   
3                    0                 0                   0                0   
4                    0                 0                   0                0   

   Auto Workshop  Automotive Shop  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  \
0              0                0          0           0       0     0    0   
1              0                0          0           0       0     0    0   
2              0                0          0           0       0     0    0   
3              0                0          0           0       0     0    0   
4              0                0          0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Stadium  Beach  Beach Bar  \
0               0                 0                   0      0          0   
1               0                 0                   0      0          0   
2               0                 0                   0      0          0   
3               0                 0                   0      0          0   
4               0                 0                   0      0          0   

   Beer Bar  Beer Store  Belgian Restaurant  Big Box Store  Bike Shop  Bistro  \
0         0           0                   0              0          0       0   
1         0           0                   0              0          0       0   
2         0           0                   0              0          0       0   
3         0           0                   0              0          0       0   
4         0           0                   0              0          0       0   

   Board Shop  Bookstore  Botanical Garden  Boutique  Bowling Alley  \
0           0          0                 0         0              0   
1           0          0                 0         0              0   
2           0          0                 0         0              0   
3           0          0                 0         0              0   
4           0          0      

In [28]:
toronto_grouped = toronto_onehot.groupby(['Borough','Neighborhood']).mean().reset_index()
toronto_grouped

Borough                     Neighborhood    ATM  \
0     Central Toronto                       Davisville  0.000   
1     Central Toronto                 Davisville North  0.000   
2     Central Toronto                        Deer Park  0.000   
3     Central Toronto         Forest Hill North & West  0.000   
4     Central Toronto            Forest Hill Road Park  0.000   
5     Central Toronto                   Forest Hill SE  0.000   
6     Central Toronto                    Lawrence Park  0.000   
7     Central Toronto                       Moore Park  0.000   
8     Central Toronto                    North Midtown  0.000   
9     Central Toronto               North Toronto West  0.000   
10    Central Toronto                        Rathnelly  0.000   
11    Central Toronto                         Roselawn  0.000   
12    Central Toronto                       South Hill  0.000   
13    Central Toronto                  Summerhill East  0.000   
14    Central Toronto                  Summerhill West  0.000   
15    Central Toronto                        The Annex  0.000   
16    Central Toronto                        Yorkville  0.000   
17   Downtown Toronto                         Adelaide  0.000   
18   Downtown Toronto                    Bathurst Quay  0.000   
19   Downtown Toronto                      Berczy Park  0.000   
20   Downtown Toronto                         CN Tower  0.000   
21   Downtown Toronto                      Cabbagetown  0.000   
22   Downtown Toronto               Central Bay Street  0.000   
23   Downtown Toronto                        Chinatown  0.000   
24   Downtown Toronto                         Christie  0.000   
25   Downtown Toronto             Church and Wellesley  0.000   
26   Downtown Toronto                   Commerce Court  0.000   
27   Downtown Toronto                  Design Exchange  0.000   
28   Downtown Toronto             First Canadian Place  0.000   
29   Downtown Toronto                  Garden District  0.000   
30   Downtown Toronto                          Harbord  0.000   
31   Downtown Toronto                     Harbourfront  0.000   
32   Downtown Toronto                Harbourfront East  0.000   
33   Downtown Toronto                Harbourfront West  0.000   
34   Downtown Toronto                   Island airport  0.000   
35   Downtown Toronto                             King  0.000   
36   Downtown Toronto                 King and Spadina  0.000   
37   Downtown Toronto                     Queen's Park  0.000   
38   Downtown Toronto                    Railway Lands  0.000   
39   Downtown Toronto                      Regent Park  0.000   
40   Downtown Toronto                         Rosedale  0.000   
41   Downtown Toronto                          Ryerson  0.000   
42   Downtown Toronto                    South Niagara  0.000   
43   Downtown Toronto                   St. James Town  0.000   
44   Downtown Toronto                  Toronto Islands  0.000   
45   Downtown Toronto                 Underground city  0.000   
46   Downtown Toronto                    Union Station  0.000   
47   Downtown Toronto                   Victoria Hotel  0.000   
48       East Toronto                     India Bazaar  0.000   
49       East Toronto                        Riverdale  0.000   
50       East Toronto                  Studio District  0.000   
51       East Toronto                      The Beaches  0.000   
52       East Toronto                 The Beaches West  0.000   
53       East Toronto                The Danforth West  0.000   
54          East York  Broadview North (Old East York)  0.000   
55          East York                     East Toronto  0.000   
56          East York                          Leaside  0.000   
57          East York                    Parkview Hill  0.000   
58          East York                 Thorncliffe Park  0.000   
59          East York                 Woodbine Gardens  0.000   
60          East York                 Woodbine He

In [63]:
num_top_venues = 5

for hood,boro in zip(toronto_grouped['Neighborhood'],toronto_grouped['Borough']):
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp = temp.iloc[2:]
    if(temp.shape[1]==3):
        temp = pd.DataFrame((temp.iloc[:,0],temp.iloc[:,1])).T
    print("----"+hood+"----"+boro+"-----")
    temp.columns = ['venue','freq']
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Davisville----Central Toronto-----
                venue  freq
0  Italian Restaurant  0.10
1    Sushi Restaurant  0.10
2         Coffee Shop  0.08
3   Indian Restaurant  0.05
4   Convenience Store  0.05


----Davisville North----Central Toronto-----
                venue  freq
0  Italian Restaurant  0.10
1    Sushi Restaurant  0.10
2         Coffee Shop  0.08
3   Indian Restaurant  0.05
4   Convenience Store  0.05


----Deer Park----Central Toronto-----
                venue  freq
0         Coffee Shop  0.12
1  Italian Restaurant  0.07
2     Thai Restaurant  0.05
3       Grocery Store  0.05
4    Sushi Restaurant  0.05


----Forest Hill North & West----Central Toronto-----
                      venue  freq
0                      Park  0.25
1                Playground  0.25
2                      Bank  0.25
3  Mediterranean Restaurant  0.25
4                       ATM  0.00


----Forest Hill Road Park----Central Toronto-----
                venue  freq
0  Light Rail Station  0.22
1  

----East Toronto----East York-----
          venue  freq
0   Pastry Shop   0.2
1          Park   0.2
2   Pizza Place   0.2
3  Liquor Store   0.2
4           Pub   0.2


----Leaside----East York-----
                     venue  freq
0        Convenience Store  0.25
1      Japanese Restaurant  0.25
2                     Park  0.25
3           Sandwich Place  0.25
4  New American Restaurant  0.00


----Parkview Hill----East York-----
                        venue  freq
0  Construction & Landscaping   1.0
1                  Nail Salon   0.0
2                 Opera House   0.0
3                      Office   0.0
4     North Indian Restaurant   0.0


----Thorncliffe Park----East York-----
                venue  freq
0   Indian Restaurant  0.12
1   Afghan Restaurant  0.08
2  Turkish Restaurant  0.08
3         Coffee Shop  0.08
4                Bank  0.08


----Woodbine Gardens----East York-----
          venue  freq
0        Bakery  0.25
1  Home Service  0.25
2          Park  0.25
3   Coffee 


----Lawrence Manor----North York-----
               venue  freq
0               Park   0.2
1         Kids Store   0.2
2               Bank   0.2
3    Doctor's Office   0.2
4  Electronics Store   0.2


----Lawrence Manor East----North York-----
               venue  freq
0               Park   0.2
1         Kids Store   0.2
2               Bank   0.2
3    Doctor's Office   0.2
4  Electronics Store   0.2


----Maple Leaf Park----North York-----
                        venue  freq
0                      Bakery  0.25
1  Construction & Landscaping  0.25
2            Business Service  0.25
3                        Park  0.25
4     New American Restaurant  0.00


----Newtonbrook----North York-----
                       venue  freq
0                Coffee Shop  0.09
1          Korean Restaurant  0.09
2  Middle Eastern Restaurant  0.06
3       Fast Food Restaurant  0.06
4             Discount Store  0.06


----North Park----North York-----
                 venue  freq
0    Convenience Store 

              venue  freq
0       Pizza Place  0.15
1  Greek Restaurant  0.06
2       Coffee Shop  0.06
3              Bank  0.06
4    Breakfast Spot  0.06


----Wexford----Scarborough-----
                       venue  freq
0                Pizza Place  0.09
1               Burger Joint  0.09
2  Middle Eastern Restaurant  0.09
3              Grocery Store  0.09
4               Intersection  0.05


----Wexford Heights----Scarborough-----
                       venue  freq
0  Middle Eastern Restaurant  0.23
1                Pizza Place  0.15
2          Indian Restaurant  0.08
3   Mediterranean Restaurant  0.08
4         Chinese Restaurant  0.08


----Woburn----Scarborough-----
                  venue  freq
0  Fast Food Restaurant  0.18
1                  Bank  0.09
2        Discount Store  0.09
3           Coffee Shop  0.09
4           Pizza Place  0.05


----Brockton----West Toronto-----
                   venue  freq
0                    Bar  0.18
1  Vietnamese Restaurant  0.12
2     

In [103]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[2:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    return row_categories_sorted.index.values[0:num_top_venues]

In [122]:
num_top_venues = 10
indicators = ['st', 'nd', 'rd']
# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.tail()

Neighborhood 1st Most Common Venue   2nd Most Common Venue  \
185  The Junction South           Coffee Shop      Italian Restaurant   
186             Trinity           Coffee Shop                    Café   
187        Mount Dennis           Pizza Place  Furniture / Home Store   
188           Runnymede           Pizza Place             Coffee Shop   
189              Weston         Train Station             Coffee Shop   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
185                   Bar    Mexican Restaurant       Thai Restaurant   
186                Museum                  Park              Boutique   
187           Coffee Shop          Tennis Court              Bus Line   
188   Fried Chicken Joint     Convenience Store         Grocery Store   
189            Laundromat                  Bank        Sandwich Place   

    6th Most Common Venue        7th Most Common Venue 8th Most Common Venue  \
185                  Café                 Antique Shop            Nail Salon   
186        Clothing Store                   Restaurant             Hotel Bar   
187         Grocery Store  Eastern European Restaurant     Electronics Store   
188        Discount Store               Sandwich Place                  Café   
189             Gift Shop               Discount Store                 Diner   

    9th Most Common Venue 10th Most Common Venue  
185         Grocery Store    Arts & Crafts Store  
186   Sporting Goods Shop      French Restaurant  
187     Elementary School   Ethiopian Restaurant  
188           Gas Station                 Bakery  
189         Grocery Store    Fried Chicken Joint

In [123]:
kclusters = 5

toronto_cluster = toronto_grouped.drop(['Neighborhood','Borough'], 1)
# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_cluster)
# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 1, 1, 0, 1, 0, 1, 0, 1, 1], dtype=int32)

In [124]:
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
manhattan_merged = df
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = manhattan_merged.join(neighborhoods_venues_sorted.set_index(['Neighborhood']), on=['Neighborhood'])
toronto_merged.dropna(inplace=True)
toronto_merged.tail(6)

index       Borough  Neighborhood   Latitude  Longitude  Cluster Labels  \
196    141  West Toronto     Runnymede  43.651703 -79.475998             1.0   
196    141  West Toronto     Runnymede  43.651703 -79.475998             1.0   
197    112          York        Weston  43.700161 -79.516247             1.0   
199    110          York     Runnymede  43.665580 -79.482108             1.0   
199    110          York     Runnymede  43.665580 -79.482108             1.0   
201    100          York  Mount Dennis  43.686960 -79.489551             1.0   

    1st Most Common Venue   2nd Most Common Venue 3rd Most Common Venue  \
196           Coffee Shop                    Café                Bakery   
196           Pizza Place             Coffee Shop   Fried Chicken Joint   
197         Train Station             Coffee Shop            Laundromat   
199           Coffee Shop                    Café                Bakery   
199           Pizza Place             Coffee Shop   Fried Chicken Joint   
201           Pizza Place  Furniture / Home Store           Coffee Shop   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
196                  Bank           Pizza Place            Shoe Store   
196     Convenience Store         Grocery Store        Discount Store   
197                  Bank        Sandwich Place             Gift Shop   
199                  Bank           Pizza Place            Shoe Store   
199     Convenience Store         Grocery Store        Discount Store   
201          Tennis Court              Bus Line         Grocery Store   

           7th Most Common Venue      8th Most Common Venue  \
196                    Gastropub  Latin American Restaurant   
196               Sandwich Place                       Café   
197               Discount Store                      Diner   
199                    Gastropub  Latin American Restaurant   
199               Sandwich Place                       Café   
201  Eastern European Restaurant          Electronics Store   

    9th Most Common Venue 10th Most Common Venue  
196    Frozen Yogurt Shop           Liquor Store  
196           Gas Station                 Bakery  
197         Grocery Store    Fried Chicken Joint  
199    Frozen Yogurt Shop           Liquor Store  
199           Gas Station                 Bakery  
201     Elementary School   Ethiopian Restaurant

In [125]:
toronto_merged['Cluster Labels'] = toronto_merged['Cluster Labels'].astype('int')

In [126]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for boro, lat, lon, poi, cluster in zip(toronto_merged['Borough'], toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi)+', ' +str(boro)+', ' + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters